In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "CI-LG_Agneby-Tiassa_colu_2012"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Cote d'Ivoire / Agneby-Tiassa / coluzzii / 2012

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          80
country                                                   Cote d'Ivoire
admin1_iso                                                        CI-LG
admin1_name                                                     Lagunes
admin2_name                                               Agneby-Tiassa
taxon                                                          coluzzii
year                                                               2012
quarter                                                              -1
cohort_label            Cote d'Ivoire / Agneby-Tiassa / coluzzii / 2012
sample_query          cohort_admin2_quarter == 'CI-LG_Agneby-Tiassa_...
latitude                                                          5.898
longitude                                                        -4.823
h12_window_size                                                  1000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id    contributor        country  location  year  \
0   AY0072-C         Tia_dPM_2  David Weetman  Cote d'Ivoire  Tiassale  2012   
1   AY0062-C        Tia_dPM_10  David Weetman  Cote d'Ivoire  Tiassale  2012   
2   AY0055-C        Tia_dPM_55  David Weetman  Cote d'Ivoire  Tiassale  2012   
3   AY0034-C        Tia_dPM_49  David Weetman  Cote d'Ivoire  Tiassale  2012   
4   AY0078-C         Tia_aPM_5  David Weetman  Cote d'Ivoire  Tiassale  2012   
..       ...               ...            ...            ...       ...   ...   
75  AY0017-C         Tia_dPM_7  David Weetman  Cote d'Ivoire  Tiassale  2012   
76  AY0043-C        Tia_dPM_34  David Weetman  Cote d'Ivoire  Tiassale  2012   
77  AY0013-C         Tia_aPM_3  David Weetman  Cote d'Ivoire  Tiassale  2012   
78  AY0036-C        Tia_aPM_10  David Weetman  Cote d'Ivoire  Tiassale  2012   
79  AY0058-C        Tia_aPM_25  David Weetman  Cote d'Ivoire  Tiassale  2012   

    month  latitude  longitude sex_call  ... admin1_name admin1_iso  \
0      -1     5.898     -4.823        F  ...     Lagunes      CI-LG   
1      -1     5.898     -4.823        F  ...     Lagunes      CI-LG   
2      -1     5.898     -4.823        F  ...     Lagunes      CI-LG   
3      -1     5.898     -4.823        F  ...     Lagunes      CI-LG   
4      -1     5.898     -4.823        F  ...     Lagunes      CI-LG   
..    ...       ...        ...      ...  ...         ...        ...   
75     -1     5.898     -4.823        F  ...     Lagunes      CI-LG   
76     -1     5.898     -4.823        F  ...     Lagunes      CI-LG   
77     -1     5.898     -4.823        F  ...     Lagunes      CI-LG   
78     -1     5.898     -4.823        F  ...     Lagunes      CI-LG   
79     -1     5.898     -4.823        F  ...     Lagunes      CI-LG   

      admin2_name     taxon  cohort_admin1_year  cohort_admin1_month  \
0   Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   
1   Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   
2   Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   
3   Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   
4   Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   
..            ...       ...                 ...                  ...   
75  Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   
76  Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   
77  Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   
78  Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   
79  Agneby-Tiassa  coluzzii     CI-LG_colu_2012      CI-LG_colu_2012   

   cohort_admin1_quarter             cohort_admin2_year  \
0        CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   
1        CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   
2        CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   
3        CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   
4        CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   
..                   ...                            ...   
75       CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   
76       CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   
77       CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   
78       CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   
79       CI-LG_colu_2012  CI-LG_Agneby-Tiassa_colu_2012   

              cohort_admin2_month          cohort_admin2_quarter  
0   CI-LG_Agneby-Tiassa_colu_2012  CI-LG_Agneby-Tiassa_colu_2012  
1   CI-LG_Agneby-Tiassa_colu_2012  CI-LG_Agneby-Tiassa_colu_2012  
2   CI-LG_Agneby-Tiassa_colu_2012  CI-LG_Agneby-Tiassa_colu_2012  
3   CI-LG_Agneby-Tiassa_colu_2012  CI-LG_Agneby-Tiassa_colu_2012  
4   CI-LG_Agneby-Tiassa_colu_2012  CI-LG_Agneby-Tiassa_colu_2012  
..                            ...                            ...  
75  CI-LG_Agneby-Tiassa_colu_2012  CI-LG_Agneby-Tiassa_colu_2012  
76  CI-LG_Agneby-Tiassa_colu_2012  CI-LG_Agneby-Tiassa_colu_2012  
77  CI-LG_Ag

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  2012     -1     80

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

(None, None)

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0  Tiassale     -4.823     5.898

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor   Study   Data release            
David Weetman Ag1000G Ag3.0         AG1000G-CI

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 80 samples from the 
*coluzzii* taxon, collected from 1 locations within the administrative 
division of Agneby-Tiassa, Lagunes, Cote d'Ivoire. Collections were made in 2012.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter    pcenter  delta_i  \
0  CI-LG_Agneby-Tiassa_colu_2012    2RL    7.676760    3838380     4385   
1  CI-LG_Agneby-Tiassa_colu_2012    2RL   56.966622   28483312     3811   
2  CI-LG_Agneby-Tiassa_colu_2012    2RL   81.861729   40930865     4931   
3  CI-LG_Agneby-Tiassa_colu_2012    2RL  120.978066   64259665     3119   
4  CI-LG_Agneby-Tiassa_colu_2012    2RL  154.386423   80963843     1063   
5  CI-LG_Agneby-Tiassa_colu_2012    2RL  166.402702   86971983     3973   
6  CI-LG_Agneby-Tiassa_colu_2012    2RL  190.291931   98916597     1805   
7  CI-LG_Agneby-Tiassa_colu_2012    2RL  204.174414  105857839     1309   
0  CI-LG_Agneby-Tiassa_colu_2012    3RL   21.940068   10970035     1310   
1  CI-LG_Agneby-Tiassa_colu_2012    3RL   38.165156   19082578     2184   
2  CI-LG_Agneby-Tiassa_colu_2012    3RL   57.170145   28585073     4963   
3  CI-LG_Agneby-Tiassa_colu_2012    3RL   64.119816   32059909     1572   
4  CI-LG_Agneby-Tiassa_colu_2012    3RL  173.456281   88910797     1388   
0  CI-LG_Agneby-Tiassa_colu_2012      X   18.376331    9188166     2184   
1  CI-LG_Agneby-Tiassa_colu_2012      X   30.257307   15128654     3909   

   stat_max    gpos_max   ppos_max  focus_gstart  focus_gstop  ...      skew  \
0    0.2662    7.243142    3621571      7.489808     7.792675  ...  0.344798   
1    0.3956   56.969424   28484712     56.905315    57.045182  ... -0.178858   
2    0.8140   81.907136   40953568     81.772461    81.932044  ...  0.172153   
3    0.9606  120.243597   63555328    120.671714   121.131242  ...  0.500000   
4    0.1328  154.413648   80977455    154.349127   154.461015  ... -0.500000   
5    0.5514  166.409574   86975418    166.334265   166.512566  ... -0.341435   
6    0.1094  190.411406   98976334    190.179904   190.411362  ... -0.046166   
7    0.1224  204.284234  105912748    203.977578   204.568088  ... -0.500000   
0    0.1336   20.171082   10085541     21.611098    22.152433  ...  0.315708   
1    0.1116   38.112112   19056056     37.729433    38.471109  ...  0.255048   
2    0.5234   57.194894   28597447     57.116494    57.202448  ...  0.365962   
3    0.1786   64.087210   32043605     64.084461    64.137494  ...  0.500000   
4    0.2484  173.490985   88928148    173.437151   173.488952  ... -0.386052   
0    0.4540   18.515120    9257560     18.249007    18.630979  ... -0.500000   
1    0.8290   30.549488   15274744     30.047050    30.570458  ... -0.287353   

   decay_left  decay_right  baseline           aic           bic        rss  \
0    0.747807     0.463661  0.030348 -17561.583631 -17533.229157   0.593935   
1    0.245231     0.314239  0.047062 -15616.315116 -15588.174960   1.024275   
2    0.357072     0.281261  0.043846 -12217.528519 -12190.552981   0.890779   
3    1.225409     0.612704  0.050392  -7273.952086  -7247.296784  12.948166   
4    0.149183     0.298367  0.042778 -17033.386196 -17005.712383   0.208126   
5    0.273747     0.439455  0.056746 -15119.184266 -15091.285872   0.863141   
6    0.448107     0.477724  0.035951 -18927.103705 -18899.126769   0.145799   
7    0.787347     1.574694  0.035393 -18324.679166 -18296.399846   0.360155   
0    1.315881     0.849458  0.025779 -16448.084055 -16420.542861   0.218759   
1    1.742889     1.223815  0.027858 -16512.122382 -16484.774111   0.142270   
2    0.214604     0.129213  0.032866 -15765.026112 -15737.384453   0.385635   
3    0.141421     0.070711  0.029185 -15193.300271 -15166.420860   0.117182   
4    0.076523     0.130682  0.031178 -15675.180633 -15647.650422   0.327284   
0    0.509296     1.018592  0.051771 -12739.729883 -12712.008223   2.222079   
1    0.841028     1.252605  0.074182 -11298.244099 -11270.433290   5.390811   

   constant_aic  bottom  top  
0 -13175.876802       0    1  
1 -11804.946321       0    1  
2  -7285.529671       0    1  
3  -4154.687324       0    1  
4 -15970.185234       0    1  
5 -11145.462039       0    1  
6 -17121.454204       0    1  
7 -17015.297778       0    1

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=True, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[5.898, -4.823], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **1,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **500**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style